<h1>Price_Prediction</h1>

<b>Description</b>:

The script takes as an input the concatenated dataframe of the footballers from the first 5 championships from Europe. The script creates a model that predicts player's value according to their abilities and age. This kind of model shall be done for every position in the game. In this example, only the strikers have been taken into consideration. 

The output of the script is a model for the strikers, and a dataset that contains the actual value of the strikers, and the predicted value of the strikers.

This is a demo, therefore only 9 leagues were taken into consideration.

In [1]:
import pandas as pd
import numpy as np
from IPython.display import display, HTML

Import concantenated dataframes from "Dataframes/Concatenated_2012.csv"

In [2]:
fp_concatenated_2012 = 'Dataframes/Concatenated_2012.csv'
concatenated_2012 = pd.read_csv(fp_concatenated_2012)

In [3]:
concatenated_2012.shape

(5264, 51)

Remove duplicate rows from the concatenated dataframe

In [4]:
# Removing duplicate rows
concatenated_2012 = concatenated_2012.drop_duplicates(subset=['Name', 'Age'])

In [5]:
concatenated_2012.shape

(5259, 51)

Extract only the strikers from the concatenated dataframe. A neural network for each position will be created.

In [6]:
result_ST_2012 = concatenated_2012[concatenated_2012['Position'].str.contains("ST")]

In [7]:
result_ST_2012.shape

(1164, 51)

In [51]:
display(HTML(result_ST_2012.to_html()))

Parse the "Value" column from dataframe. Transform the strings containing "M" to 1.000.000, "K" to 1000.

In [8]:
# Function to convert string values to float
def convert_to_float(string_value):
    string_value = string_value.strip()  # Remove leading and trailing whitespace
    if string_value == '-':
        return np.nan  # Treat '-' as NaN (Not a Number)
    multiplier = 1
    if string_value.endswith('M'):
        multiplier = 1000000
        string_value = string_value[:-1]
    elif string_value.endswith('K'):
        multiplier = 1000
        string_value = string_value[:-1]
    try:
        return float(string_value.replace('$', '')) * multiplier
    except ValueError:
        return np.nan  # Handle any other non-numeric values as NaN

# Apply the function to the 'A' column
result_ST_2012['Value_float'] = result_ST_2012['Value'].apply(convert_to_float)

c:\users\hp\appdata\local\programs\python\python36\lib\site-packages\ipykernel_launcher.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


"Value_float" column contains the value of football players in floating point numbers.

In [9]:
display(HTML(result_ST_2012.to_html()))

Sort in descending order by price

In [10]:
result_ST_2012 = result_ST_2012.sort_values(by='Value_float', ascending=False)

In [13]:
display(HTML(result_ST_2012.to_html()))

Columns to drop from strikers. These columns are goalkeeper columns, like Aerial Ability, Handling, Kicking, Reflexes.

In [11]:
columns_to_drop = ['Aer', 'Cmd', 'Com', 'Ecc', 'Han', 'Kic', 'One', 'Ref', 'Rus', 'Pun', 'Thr']
result_ST_2012 = result_ST_2012.drop(columns=columns_to_drop)

In [55]:
display(HTML(result_ST_2012.to_html()))

Search for NaN (Not a number) values in the "Value_float" column

In [12]:
# Column to search for NaN values
column_to_search = 'Value_float'

# Boolean indexing to find NaN values in the specified column
nan_values = result_ST_2012[result_ST_2012[column_to_search].isna()]

# Display rows with NaN values in column_to_search
print(nan_values)

                           Name  Acc  Agi  Bal  Jum  Nat  Pac  Sta  Str  Agg  \
1881   Samuel Castillejo          12   11    9   10    4   10    7    2   14   
1885   Juan Carlos                11    7    6    8   17   10    3    1    7   
1887   ?lex Serrano               10   10    9    8   12   13    9    5   11   

      ...    LTh    Mar    Pas  Pen    Tac  Tec                      Position  \
1881  ...   1      2      9       4   7      12   AM (C), ST                    
1885  ...   1      3      3       3   1       9   ST                            
1887  ...   1      4      12     10   9      12   AM (C), ST                    

      Age      Value  Value_float  
1881   16   -                 NaN  
1885   16   -                 NaN  
1887   16   -                 NaN  

[3 rows x 41 columns]


In [13]:
# Column with NaN values to drop rows
column_to_check = 'Value_float'

# Drop rows with NaN values in column X
result_ST_2012 = result_ST_2012.dropna(subset=[column_to_check])

In [14]:
result_ST_2012.shape

(1161, 41)

In [15]:
import numpy as np
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense

Select input columns for the neural network

In [16]:
# Columns
all_input_cols =      ['Name',
                        'Acc', 
                        'Agi', 
                        'Bal',
                        'Jum',
                        'Nat',
                        'Pac',
                        'Sta',
                        'Str',
                        'Agg',
                        'Ant',
                        'Bra',
                        'Cmp',
                        'Cnt',
                        'Cre',
                        'Dec',
                        'Det',
                        'Fla',
                        'Inf',
                        'Off',
                        'Pos',
                        'Tea',
                        'Wor',
                        'Cor',
                        'Cro',
                        'Dri',
                        'Fin',
                        'Fir',
                        'Fre',
                        'Hea',
                        'Lon',
                        'LTh',
                        'Mar',
                        'Pas',
                        'Pen',
                        'Tac',
                        'Tec',
                        'Age',
                        'Position',
                       ]

Separate input features and output (target) features 

In [17]:
# Separate features (input) and target (output)
X = result_ST_2012[all_input_cols]
y = result_ST_2012['Value_float']

In [23]:
display(HTML(X.to_html()))

In [25]:
y

0       80000000.0
1       62000000.0
2       56000000.0
3       51000000.0
4       50000000.0
           ...    
1183        7000.0
1179        7000.0
1175        7000.0
1294        5000.0
1295        5000.0
Name: Value_float, Length: 286, dtype: float64

In [18]:
X = X.values
y = y.values

Train test split. Split data into training set and testing set (20% training samples)

In [19]:
# Split the data into training and testing sets
X_train_original, X_test_original, y_train_original, y_test_original = train_test_split(X, y, test_size=0.2, random_state=42)

After splitting the data, convert back to dataframes

In [20]:
# Convert NumPy array to DataFrame
df_X_train_original = pd.DataFrame(data=X_train_original)
df_X_test_original = pd.DataFrame(data=X_test_original)
df_y_train_original = pd.DataFrame(data=y_train_original)
df_y_test_original = pd.DataFrame(data=y_test_original)

In [21]:
# Assign column names to DataFrame
df_X_train_original.columns = all_input_cols
df_X_test_original.columns = all_input_cols
df_y_train_original.columns = ['Value_float']
df_y_test_original.columns = ['Value_float']

In [22]:
# Columns
original_cols =      [ 'Acc', 
                        'Agi', 
                        'Bal',
                        'Jum',
                        'Nat',
                        'Pac',
                        'Sta',
                        'Str',
                        'Agg',
                        'Ant',
                        'Bra',
                        'Cmp',
                        'Cnt',
                        'Cre',
                        'Dec',
                        'Det',
                        'Fla',
                        'Inf',
                        'Off',
                        'Pos',
                        'Tea',
                        'Wor',
                        'Cor',
                        'Cro',
                        'Dri',
                        'Fin',
                        'Fir',
                        'Fre',
                        'Hea',
                        'Lon',
                        'LTh',
                        'Mar',
                        'Pas',
                        'Pen',
                        'Tac',
                        'Tec',
                        'Age',
                       ]

In [23]:
# Convert NumPy array to DataFrame
df_orig_X_train_original = df_X_train_original[original_cols]
df_orig_X_test_original = df_X_test_original[original_cols]
df_orig_y_train_original = df_y_train_original['Value_float']
df_orig_y_test_original = df_y_test_original['Value_float']

In [24]:
df_orig_X = pd.concat([df_orig_X_train_original, df_orig_X_test_original])

In [25]:
df_orig_X.shape

(1161, 37)

In [26]:
df_orig_y = pd.concat([df_orig_y_train_original, df_orig_y_test_original])

In [27]:
df_orig_y.shape

(1161,)

Scale data from the columns: attributes, age and value

In [28]:
# Columns to be normalized
columns_to_scale = ['Acc', 
                        'Agi', 
                        'Bal',
                        'Jum',
                        'Nat',
                        'Pac',
                        'Sta',
                        'Str',
                        'Agg',
                        'Ant',
                        'Bra',
                        'Cmp',
                        'Cnt',
                        'Cre',
                        'Dec',
                        'Det',
                        'Fla',
                        'Inf',
                        'Off',
                        'Pos',
                        'Tea',
                        'Wor',
                        'Cor',
                        'Cro',
                        'Dri',
                        'Fin',
                        'Fir',
                        'Fre',
                        'Hea',
                        'Lon',
                        'LTh',
                        'Mar',
                        'Pas',
                        'Pen',
                        'Tac',
                        'Tec',
                        'Age',
                       ]

Convert data to float64

In [29]:
# Convert columns 'A', 'B', and 'C' to float64
for column in columns_to_scale:
    df_X_train_original[column] = df_X_train_original[column].astype('float64')
    df_X_test_original[column] = df_X_test_original[column].astype('float64')
    
df_y_train_original['Value_float'] = df_y_train_original['Value_float'].astype('float64')
df_y_test_original['Value_float'] = df_y_test_original['Value_float'].astype('float64')

Apply min-max scaling

In [30]:
# Min-max scaling for columns 'A', 'B', and 'C'
for column in columns_to_scale:
    min_val = df_X_train_original[column].min()
    max_val = df_X_train_original[column].max()
    df_X_train_original[column] = (df_X_train_original[column] - min_val) / (max_val - min_val)
    
    min_val = df_X_test_original[column].min()
    max_val = df_X_test_original[column].max()
    df_X_test_original[column] = (df_X_test_original[column] - min_val) / (max_val - min_val)

# min_val = df_y_train_original['Value_float'].min()
# max_val = df_y_train_original['Value_float'].max()
# df_y_train_original['Value_float'] = (df_y_train_original['Value_float'] - min_val) / (max_val - min_val)

# min_val = df_y_test_original['Value_float'].min()
# max_val = df_y_test_original['Value_float'].max()
# df_y_test_original['Value_float'] = (df_y_test_original['Value_float'] - min_val) / (max_val - min_val)

df_y_train_original['Value_float'] = df_y_train_original['Value_float'] / 80000000
df_y_test_original['Value_float'] = df_y_test_original['Value_float'] /80000000

In [31]:
X_train_original = df_X_train_original.values
X_test_original = df_X_test_original.values
y_train_original = df_y_train_original.values
y_test_original = df_y_test_original.values

Remove "Name" and "Position" columns

In [32]:
# Remove the first and last columns
X_train_new = X_train_original[:, 1:-1]
X_test_new = X_test_original[:, 1:-1]

y_train_new = y_train_original
y_test_new = y_test_original

Convert data to float64

In [33]:
X_train_new = X_train_new.astype('float64')
X_test_new = X_test_new.astype('float64')

y_train_new = y_train_new.astype('float64')
y_test_new = y_test_new.astype('float64')

Define the neural network model.

<ul>
    <li>Number of inputs: 37</li>
    <li>Number of outputs: 1</li>
    <li>Activations: ReLu for inner neurons, and Sigmoid for the output layer</li>
    <li>Loss: Mean squared error</li>
    <li>Optimizer: Adam</li>
    <li>Number of epochs: 100</li>
</ul>

In [34]:
# Define the neural network model
model = Sequential([
    Dense(64, activation='relu', input_shape=(37,)),  # 37 input features
    Dense(64, activation='relu'),
    Dense(1, activation='sigmoid')  # Output layer with 1 neuron for Price prediction
])

# Compile the model
model.compile(optimizer='adam', loss='mean_squared_error')

# Train the model
model.fit(X_train_new, y_train_new, epochs=100, batch_size=1, verbose=1)

# Evaluate the model
loss = model.evaluate(X_test_new, y_test_new, verbose=0)
print("Test loss:", loss)

Epoch 1/100
928/928 [==============================] - 1s 604us/step - loss: 0.0123
Epoch 2/100
928/928 [==============================] - 1s 620us/step - loss: 0.0081
Epoch 3/100
928/928 [==============================] - 1s 629us/step - loss: 0.0081
Epoch 4/100
928/928 [==============================] - 1s 606us/step - loss: 0.0073
Epoch 5/100
928/928 [==============================] - 1s 613us/step - loss: 0.0070
Epoch 6/100
928/928 [==============================] - 1s 631us/step - loss: 0.0066
Epoch 7/100
928/928 [==============================] - 1s 631us/step - loss: 0.0062
Epoch 8/100
928/928 [==============================] - 1s 630us/step - loss: 0.0057
Epoch 9/100
928/928 [==============================] - 1s 625us/step - loss: 0.0060
Epoch 10/100
928/928 [==============================] - 1s 645us/step - loss: 0.0053
Epoch 11/100
928/928 [==============================] - 1s 629us/step - loss: 0.0054
Epoch 12/100
928/928 [==============================] - 1s 645us/step - lo

Save model to disk

In [35]:
from tensorflow.keras.models import Sequential, model_from_json

# serialize model to JSON
model_json = model.to_json()
with open("Models/strikers_model_2012.json", "w") as json_file:
    json_file.write(model_json)
# serialize weights to HDF5
model.save_weights("Models/strikers_model_2012.h5")
print("Saved model to disk")

Saved model to disk


Load model from disk

In [36]:
# load json and create model
json_file = open('Models/strikers_model_2012.json', 'r')
loaded_model_json = json_file.read()
json_file.close()
model = model_from_json(loaded_model_json)
# load weights into new model
model.load_weights("Models/strikers_model_2012.h5")
print("Loaded model from disk")

Loaded model from disk


Predict price for the test dataset

In [82]:
# Make predictions
predicted_price = model.predict(X_test_new)

Recreate the original dataframes, with the original, non-scaled values

In [83]:
columns_dataframe_y = [
    'Value'
]

df_ST_2012_y_train = pd.DataFrame(y_train_original, columns=columns_dataframe_y)
df_ST_2012_y_test = pd.DataFrame(y_test_original, columns=columns_dataframe_y)

In [84]:
df_ST_2012_y = pd.concat([df_ST_2012_y_train, df_ST_2012_y_test])

In [85]:
# Create DataFrame
columns_dataframe = ['Name',
            'Acc', 
            'Agi', 
            'Bal',
            'Jum',
            'Nat',
            'Pac',
            'Sta',
            'Str',
            'Agg',
            'Ant',
            'Bra',
            'Cmp',
            'Cnt',
            'Cre',
            'Dec',
            'Det',
            'Fla',
            'Inf',
            'Off',
            'Pos',
            'Tea',
            'Wor',
            'Cor',
            'Cro',
            'Dri',
            'Fin',
            'Fir',
            'Fre',
            'Hea',
            'Lon',
            'LTh',
            'Mar',
            'Pas',
            'Pen',
            'Tac',
            'Tec',
            'Age',
            'Position'
]

df_ST_2012_X_train = pd.DataFrame(X_train_original, columns=columns_dataframe)
df_ST_2012_X_test = pd.DataFrame(X_test_original, columns=columns_dataframe)

In [86]:
df_ST_2012_X = pd.concat([df_ST_2012_X_train, df_ST_2012_X_test])

In [87]:
# Concatenate df1 and df2 along the columns (axis=1)
df_ST_2012 = pd.concat([df_ST_2012_X, df_ST_2012_y], axis=1)

Predict price for the train dataset

In [88]:
predicted_price = model.predict(X_train_new)

In [89]:
columns_dataframe_predicted_train = [
    'Predicted_value'
]

df_ST_2012_predicted_train = pd.DataFrame(predicted_price, columns=columns_dataframe_predicted_train)

Predict price for the test dataset

In [90]:
predicted_price = model.predict(X_test_new)

In [91]:
columns_dataframe_predicted_test = [
    'Predicted_value'
]

df_ST_2012_predicted_test = pd.DataFrame(predicted_price, columns=columns_dataframe_predicted_test)

Concatenate the predicted train and test values

In [92]:
# Append df2 to df1
df_ST_2012_predicted = df_ST_2012_predicted_train.append(df_ST_2012_predicted_test, ignore_index=True)

Add the prediction column to the original dataframe

In [93]:
# Reset indices of the DataFrames
df_ST_2012.reset_index(drop=True, inplace=True)
df_ST_2012_predicted.reset_index(drop=True, inplace=True)

# Concatenate df1 and df2 along the columns (axis=1)
df_ST_2012 = pd.concat([df_ST_2012, df_ST_2012_predicted], axis=1)

Create a column "Difference" that contains the difference between the original value and the predicted value

In [94]:
# Create a new column 'difference' with the difference between 'a' and 'b'
df_ST_2012['Difference'] = df_ST_2012['Predicted_value'] - df_ST_2012['Value']

Scale the columns "Value", "Predicted_value" and "Difference" back to the original values.

In [95]:
# Columns to convert and multiply
columns_to_convert = ['Value',
                      'Predicted_value',
                      'Difference']

# Convert columns to int and multiply by 20
df_ST_2012[columns_to_convert] = (df_ST_2012[columns_to_convert] * 80)

In [96]:
# Columns
original_cols =      [ 'Acc', 
                        'Agi', 
                        'Bal',
                        'Jum',
                        'Nat',
                        'Pac',
                        'Sta',
                        'Str',
                        'Agg',
                        'Ant',
                        'Bra',
                        'Cmp',
                        'Cnt',
                        'Cre',
                        'Dec',
                        'Det',
                        'Fla',
                        'Inf',
                        'Off',
                        'Pos',
                        'Tea',
                        'Wor',
                        'Cor',
                        'Cro',
                        'Dri',
                        'Fin',
                        'Fir',
                        'Fre',
                        'Hea',
                        'Lon',
                        'LTh',
                        'Mar',
                        'Pas',
                        'Pen',
                        'Tac',
                        'Tec',
                        'Age',
                       ]

In [97]:
df_ST_2012 = df_ST_2012.drop(columns=original_cols)

Add back the original, non-scaled columns

In [98]:
# Reset indices of the DataFrames
df_ST_2012.reset_index(drop=True, inplace=True)
df_orig_X.reset_index(drop=True, inplace=True)

# Concatenate df1 and df2 along the columns (axis=1)
df_ST_2012 = pd.concat([df_ST_2012, df_orig_X], axis=1)

Rearrange columns

In [99]:
# Rearrange columns
cols_to_move_right = ['Position', 'Value','Predicted_value','Difference']
cols_left = [col for col in df_ST_2012.columns if col not in cols_to_move_right]

# Reorganize DataFrame columns
df_ST_2012 = df_ST_2012[cols_left + cols_to_move_right]

Save the strikers dataframe with the predicted values in .csv file

In [104]:
# Save DataFrame to a CSV file with UTF-8 encoding
df_ST_2012.to_csv('Results/strikers_2012_utf.csv', index=False, encoding='utf-8')

In [101]:
import unicodedata

df_ST_2012['Name'] = df_ST_2012['Name'].apply(lambda x: unicodedata.normalize('NFKD', x).encode('ascii', 'ignore').decode('utf-8'))

Display the football players, based on the difference between original value and predicted value.

Sort type:
<ul>
    <li>Ascending = False: underrated players are in the top.</li>
    <li>Ascending = True: overrated players are in the top.</li>
</ul>

In [103]:
from IPython.display import display, HTML

df_ST_2012 = df_ST_2012.sort_values(by='Difference', ascending=False)

display(HTML(df_ST_2012.to_html()))